In [2]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
import plotly.graph_objects as go
import plotly.io as py


def plot_utility(file_path, label):
    # Constants
    tau = 1  # Length of the interval
    T = 1  # Target response time

    # Read result file
    results = pd.read_csv(file_path, 
                          usecols=[0, 1, 6],
                          header=None,
                          names=['image_number', 'avg_confidence', 'response_time'],
                          dtype={'avg_confidence': np.float32, 'response_time': np.float32})

    # Set the DataFrame's index to be the image_number
    results.set_index('image_number', inplace=True)

    # Reindex the DataFrame to fill in missing image numbers
    results = results.reindex(np.arange(1, results.index.max() + 1), fill_value=0)

    # Now, the DataFrame should have no missing image numbers, and missing rows are filled with zeros
    response_times = results['response_time']
    confidence_scores = results['avg_confidence']

    # Calculate delay
    r = response_times.values
    #a = average_request_rate
    C = confidence_scores.values
    # Constants for the piecewise function
    Rmax = 1  # Maximum acceptable response time
    Rmin = 0.1  # Minimum acceptable response time
    Cmax = 1  # Maximum acceptable confidence score
    Cmin = 0.5 # Minimum acceptable confidence score

    # Penalties for exceeding thresholds
    pdv = 1  # Penalty for exceeding the response time threshold
    pev = 1  # Penalty for exceeding the confidence score threshold

    # Weights for the response time and confidence score in the utility function
    we = 0.5 #Confidence
    wd = 0.5 #Response Time

    # Calculate the piecewise functions for response time and confidence score
    # Calculate the piecewise function for response time
    Tτ = np.empty_like(r)
    for i in range(len(r)):
        if r[i] > Rmax:
            Tτ[i] = (Rmax - r[i]) * pdv
        elif Rmin <= r[i] <= Rmax:
            Tτ[i] = r[i]
        else:  # r[i] < Rmin
            Tτ[i] = (r[i] - Rmin) * pdv

    # Calculate the piecewise function for confidence score
    Eτ = np.empty_like(C)
    for i in range(len(C)):
        if C[i] > Cmax:
            Eτ[i] = (Cmax - C[i]) * pev
        elif Cmin <= C[i] <= Cmax:
            Eτ[i] = C[i]
        else:  # C[i] < Cmin
            Eτ[i] = (C[i] - Cmin) * pev

    # Calculate the utility values using the piecewise functions
    utility_values = we * Eτ + wd * Tτ

    #utility_values = tau * np.where(r <= T, C, C)
    
    final_utility = np.sum(utility_values)
    #print(f"Final utility for {label}: {final_utility}")

    # Return both utility values and final utility for plotting and annotation
    return np.cumsum(utility_values), final_utility


# Call the function for each data file
Nano_model, nano_utility = plot_utility('../Results/Nano_log.csv', 'Nano Model')
Naive, navie_utility = plot_utility('../Results/NAVIE_log.csv', 'Navie_Approach')
AdaMLS, AdaMLS_utility = plot_utility('../Results/AdaMLS_log.csv', 'AdaMLS Approach')

# Create a plotly graph object
fig = go.Figure()

# Add traces
fig.add_trace(go.Scatter(y=Nano_model, mode='lines', name='Nano Model'))
fig.add_trace(go.Scatter(y=Naive, mode='lines', name='Naive Approach'))
fig.add_trace(go.Scatter(y=AdaMLS, mode='lines', name='AdaMLS Approach'))


#fig.add_trace(go.Scatter(y=small_model, mode='lines', name='Small Model'))
#fig.add_trace(go.Scatter(y=medium_model, mode='lines', name='Medium Model'))

# Add labels and title
fig.update_layout(
    xaxis_title="Number of Images Processed",
    yaxis_title="Utility",
    autosize=False,
    width=1000,  # adjust these values as per your needs
    height=600,
    legend=dict(title="Approach", y=0.05, x=0.05),  # Place legend inside plot at bottom left
    font=dict(
        family="Courier New, monospace",
        size=18,
        color="Black"
    ),
    annotations=[
        dict(
            x=0,
            y=1,
            xref='paper',
            yref='paper',
            text=f"Navie Total Utility: {navie_utility:.2f}<br>"
                 f"Nano Model Total Utility: {nano_utility:.2f}<br>"
                 f"AdaMLS Total Utility: {AdaMLS_utility:.2f}<br>",
            showarrow=False,
            align="left",
            font=dict(
                size=16,
            ),
        )
    ]
)

# Save the figure in high resolution
py.write_image(fig, 'Utility.png', width=1000, height=600, scale=20)

# Show the plot
fig.show()